# Combining MQTT and Convolutional Model

In [1]:
import tensorflow as tf
import cv2
import numpy as np
import matplotlib.pyplot as plt
import paho.mqtt.client as mqtt
import time

#loading the model
model = tf.keras.models.load_model("C:/Users/AKUMA/Desktop/DESKTOP/UNITY/Python Scripts/mnist_digit_recog_cnn_2-conv-128-nodes-1-dense-17-04-2020_00-09_Ver16.h5")


In [2]:
#_______________________________________________________________________________________________________
#creating empty payload variable, will be filed by on_message 
prediction = ""
payload = ""
validation_color = (0,0,0)
broker = "broker.hivemq.com"
topic = "ROB-ASSIST/AUTO/DROPDOWN"
topic1 = "ROB-ASSIST/DEBUG"
client = mqtt.Client("ROB-ASSIST")




#_______________________________________________________________________________________________________

def on_log(client, userdata, level, buf):
    print("-------------------on_log debug---------------------")
    print("log",buf)
    print("----------------------------------------------------")

#_______________________________________________________________________________________________________
# The callback for when the client receives a CONNACK response from the server.

def on_connect(client, userdata, flags, rc):
    print("---------------on_connect debug---------------------")
    print("Connected with result code ", str(rc))
    print("----------------------------------------------------")

    

    
#_______________________________________________________________________________________________________
# action to take when a payload is receive
    
def on_payload():   
        
    if payload == str(prediction):
        text = ("SPOT FOUND: " + str(prediction))
        validation_color = (0, 255, 0)
    else:
        text = "NO SPOT DETECTED."
        validation_color = (255, 255, 255)

    #send Opencv ACK
    client.publish(topic1, text, qos=0, retain=False)
      
    #return value for camera UI
    return text, validation_color

#_______________________________________________________________________________________________________
# The callback for when a PUBLISH message is received from the server.

def on_message(client, userdata, msg):
    
    #storing payload message
    global payload
    payload = str(msg.payload.decode("utf-8"))    

    #debug
    print("---------------on_message debug---------------------")
    print("payload receive: ", str(msg.payload))
    print("message topic= ",       msg.topic)
    print("message qos= ",         msg.qos)
    print("message retain flag= ", msg.retain)
    print("----------------------------------------------------")
      
        
    #on payload run this function
    on_payload()
    
    
#_______________________________________________________________________________________________________
# connection to broker and running the loop

try:
    client.connect(broker,port=1883) #connect to broker
    print("connected to ", broker)
except:
    print("connection failed")
    exit(1) #Should quit or raise flag to quit or retry
    
    
    
client.on_message = on_message
client.subscribe(topic)
client.on_log = on_log
client.loop_start()
#client.loop_stop()
#client.disconnect()


#publish


connected to  broker.hivemq.com


In [3]:
# with default trackbar value..
# - camera has to be between 20 and 40cm from the target
# - digit has to be in 8x8 cm box

# how to read box coordinates ; https://stackoverflow.com/questions/29739411/what-does-cv2-cv-boxpointsrect-return/51952289

VideoCapture = cv2.VideoCapture(0)
color = (255,255,255)
thickness = 2

def empty():
    pass
    
windowName = "parameters"
cv2.namedWindow(windowName)
cv2.resizeWindow(windowName, 800,550)


cv2.createTrackbar("pixel_neighboors", windowName, 73, 500, empty) 
cv2.createTrackbar("Constant", windowName, 4, 500, empty) 
cv2.createTrackbar("blur", windowName, 8, 100, empty) 
cv2.createTrackbar("area min", windowName, 327, 10000, empty)
cv2.createTrackbar("area max", windowName, 2675, 10000, empty)
cv2.createTrackbar("rectangle length min", windowName, 250, 10000, empty)
cv2.createTrackbar("rectangle length max", windowName, 700, 10000, empty)
cv2.createTrackbar("x length", windowName, 457, 1000, empty)
cv2.createTrackbar("y length", windowName, 388, 1000, empty)
   
    
    
while True:
#__________________________________________________________________________________________________________________                        
# setting up parameters

    # storing trackbar value in variables
    pixel_neighboors_value  = cv2.getTrackbarPos("pixel_neighboors", windowName)
    Constant_value          = cv2.getTrackbarPos("Constant", windowName)
    blur_value              = cv2.getTrackbarPos("blur", windowName)
    threshold_area_min      = cv2.getTrackbarPos("area min", windowName)
    threshold_area_max      = cv2.getTrackbarPos("area max", windowName)
    rect_length_min         = cv2.getTrackbarPos("rectangle length min", windowName)
    rect_length_max         = cv2.getTrackbarPos("rectangle length max", windowName)
    threshold_x_length      = cv2.getTrackbarPos("x length", windowName)
    threshold_y_length      = cv2.getTrackbarPos("y length", windowName)
    
    
    # need those conditions otherwise some variables will raise errors
    if blur_value < 2:
        blur_value = 2
        
    if  (pixel_neighboors_value % 2) == 0:
        pixel_neighboors_value = 7
        
    elif pixel_neighboors_value < 1:
        pixel_neighboors_value = 7

    # recognized digit (and false positives) will be stocked here, it will be emptied at the beginning of each frame
    preprocessed_digits = []
    
    
    
#__________________________________________________________________________________________________________________                        
# beginning image processing


    # reading video feed
    ret, frame = VideoCapture.read()
    
    # defining width and height of the camera
    frame_width, frame_height, frame_channel = frame.shape
                            
    #setting up screen limits for bounding box detections 
    start_point_1 = (int(frame_width/2 + frame_width/2), 0)
    end_point_1   = (int(frame_width/2 + frame_width/2), frame_height)

    start_point_2 = (int(frame_width/4), 0)
    end_point_2   = (int(frame_width/4), frame_height)

    cv2.line(frame, start_point_1, end_point_1, color, thickness)                     
    cv2.line(frame, start_point_2, end_point_2, color, thickness)                     

    
    # frame converted to grayscale
    gray = cv2.cvtColor(frame, cv2.COLOR_BGR2GRAY)
    
    # frame blured by default kernel size 8
    blur = cv2.blur(gray,(blur_value,blur_value))

    # cv2.adaptiveThreshold(src, maxValue, adaptiveMethod, thresholdType, blockSize, C)
    # maxValue is the pixel value give to the pixel above the treshold
    # block Size is the number of neighboring pixels, it makes binary object thicker (it only accepts odd values)    
    # C is a constant that actually acts like a noise reductor
    # this type of threshold acts better with variable light source
    adaptive_threshold = cv2.adaptiveThreshold(blur, 255, cv2.ADAPTIVE_THRESH_GAUSSIAN_C, cv2.THRESH_BINARY_INV, pixel_neighboors_value, Constant_value)

    # cv2.findContours(image, mode, method, contours, hierarchy, offset) 
    # mode is the way of finding contours, and method is the approximation method for the detection. 
    contours, hierachy = cv2.findContours(adaptive_threshold, cv2.RETR_TREE, cv2.CHAIN_APPROX_SIMPLE )


#__________________________________________________________________________________________________________________                        
# getting contours coordinates

    for points in contours:
        
        # obtains the 4 corner points of the contour rectangle.    
        x,y,w,h = cv2.boundingRect(points) 
        
        # area is x length times y lengths)
        area = int(cv2.contourArea(points))
        #cv2.putText(frame, str(area), (x,y), cv2.FONT_HERSHEY_PLAIN, 1, (255,255,255), 2)
        
        # rectangle length is the length of a closed rectangle
        rectangle_length = int(cv2.arcLength(points, True))
        #cv2.putText(frame, str(rectangle_length), (x + 20 ,y + 20), cv2.FONT_HERSHEY_PLAIN, 1, (0,255,255), 2)
        
        
        
        
#__________________________________________________________________________________________________________________                        
# set threshold conditions for filter the detected rectangles

        if area > threshold_area_min and area < threshold_area_max:
            if rectangle_length > rect_length_min and rectangle_length < rect_length_max:
                  if x + w < threshold_x_length and y + h < threshold_y_length:
                    if x < int(frame_width/2 + frame_width/2) and x > int(frame_width/4):
                 
                
                
                        # digit pre-processing
                        # Cropping out the digit from the thresholding image
                        ROI = adaptive_threshold[y:y+h, x:x+w]    
                        cv2.imshow("ROI", ROI)
                       
                        # Resizing the digit to (18, 18)
                        resized_digit = cv2.resize(ROI, (18,18))   
                        #cv2.imshow("resized", resized_digit)

                        # Padding the digit with 5 pixels of black color (zeros) in each side to produce the image of (28, 28)
                        padded_digit = np.pad(resized_digit, ((5,5),(5,5)), "constant", constant_values=0)
                        #cv2.imshow("padded", padded_digit)

                        # Adding the preprocessed digit to the list of preprocessed digits
                        preprocessed_digits.append(padded_digit)

                        #setting coordinates                    
                        start = (x, y)
                        end = (w + x, h + y)

                        #drawing bounding box around detected objects
                        cv2.rectangle(frame, start, end, color, thickness)

                        
                        #cv2.drawContours(frame, contours, contourIdx = -1, color = (255, 0, 0), thickness = 2)
                         
                        
#__________________________________________________________________________________________________________________                        
# make the prediction

                        
                        for digit in preprocessed_digits:
                            prediction_softmax = model.predict(digit.reshape(1, 28, 28, 1))  
                        
                        prediction = np.argmax(prediction_softmax)
                        prediction_class = "Final Output: {}".format(np.argmax(prediction_softmax)) 
                        cv2.putText(frame, prediction_class, (x,y), cv2.FONT_HERSHEY_PLAIN, 1, (255,255,255), 2)
                    
    text, validation_color = on_payload()
    full_text = (text + str(prediction))
    cv2.putText(frame, text, (int(frame_width/2), 50), cv2.FONT_HERSHEY_PLAIN, 1, validation_color, 2)
    


#__________________________________________________________________________________________________________________                        
# Debug windows
        
    cv2.imshow('frame', frame)
    cv2.imshow('thres', adaptive_threshold)

    if cv2.waitKey(1) == ord('q'):
        break
        
VideoCapture.release()
cv2.destroyAllWindows()


-------------------on_log debug---------------------
log Received CONNACK (0, 0)
----------------------------------------------------
-------------------on_log debug---------------------
log Received SUBACK
----------------------------------------------------
-------------------on_log debug---------------------
log Received PUBLISH (d0, q0, r1, m0), 'ROB-ASSIST/AUTO/DROPDOWN', ...  (1 bytes)
----------------------------------------------------
---------------on_message debug---------------------
payload receive:  b'3'
message topic=  ROB-ASSIST/AUTO/DROPDOWN
message qos=  0
message retain flag=  1
----------------------------------------------------
-------------------on_log debug---------------------
log Sending PUBLISH (d0, q0, r0, m2), 'b'ROB-ASSIST/DEBUG'', ... (17 bytes)
----------------------------------------------------
-------------------on_log debug---------------------
log Sending PUBLISH (d0, q0, r0, m3), 'b'ROB-ASSIST/DEBUG'', ... (17 bytes)
-------------------------------

TypeError: empty() takes 0 positional arguments but 1 was given

-------------------on_log debug---------------------
log Sending PUBLISH (d0, q0, r0, m24556), 'b'ROB-ASSIST/DEBUG'', ... (13 bytes)
----------------------------------------------------


TypeError: empty() takes 0 positional arguments but 1 was given

-------------------on_log debug---------------------
log Sending PUBLISH (d0, q0, r0, m24557), 'b'ROB-ASSIST/DEBUG'', ... (17 bytes)
----------------------------------------------------
-------------------on_log debug---------------------
log Sending PUBLISH (d0, q0, r0, m24558), 'b'ROB-ASSIST/DEBUG'', ... (17 bytes)
----------------------------------------------------


TypeError: empty() takes 0 positional arguments but 1 was given

-------------------on_log debug---------------------
log Sending PUBLISH (d0, q0, r0, m24559), 'b'ROB-ASSIST/DEBUG'', ... (17 bytes)
----------------------------------------------------
-------------------on_log debug---------------------
log Sending PUBLISH (d0, q0, r0, m24560), 'b'ROB-ASSIST/DEBUG'', ... (17 bytes)
----------------------------------------------------
-------------------on_log debug---------------------
log Sending PUBLISH (d0, q0, r0, m24561), 'b'ROB-ASSIST/DEBUG'', ... (17 bytes)
----------------------------------------------------
-------------------on_log debug---------------------
log Sending PUBLISH (d0, q0, r0, m24562), 'b'ROB-ASSIST/DEBUG'', ... (17 bytes)
----------------------------------------------------
-------------------on_log debug---------------------
log Sending PUBLISH (d0, q0, r0, m24563), 'b'ROB-ASSIST/DEBUG'', ... (17 bytes)
----------------------------------------------------
-------------------on_log debug---------------------
log Sending PUBLI